## Inisialisasi Library

In [6]:
import cv2
import numpy as np
# import pymysql
from datetime import datetime

## Sumber Video (Live atau Lokal Video)

In [7]:
cap = cv2.VideoCapture('pagi.mp4')  # 0/1 untuk webcam

## mendapatkan tinggi dan lebar video

In [8]:
# Get original width and height
ret, frame = cap.read()
if not ret:
    print("Failed to read from video source.")
    exit()

height2, width2, channels = frame.shape

## Background subtractor , background static

In [9]:
fgbg = cv2.createBackgroundSubtractorMOG2()

## Tracking Kenderaan, setup ruas jalan dan pixel travel(untuk menghitung kecepatan kenderaan)

In [10]:
# Vehicle tracking and speed
vehicle_id_counter = 0
tracker_dict = {}
speed_line_y1 = 245
speed_line_y2 = 355
meters_travel_pixel = 0.2

last_vehicle_ids_in_zone = set()


## Proses Video

In [11]:
while True:
    ret, frame = cap.read()
    if not ret:
        break

    gray = cv2.cvtColor(frame, cv2.COLOR_BGR2GRAY)
    fgmask = fgbg.apply(gray)

    kernel = cv2.getStructuringElement(cv2.MORPH_ELLIPSE, (5, 5))
    closing = cv2.morphologyEx(fgmask, cv2.MORPH_CLOSE, kernel)
    opening = cv2.morphologyEx(closing, cv2.MORPH_OPEN, kernel)
    dilation = cv2.dilate(opening, kernel)
    _, bins = cv2.threshold(dilation, 220, 255, cv2.THRESH_BINARY)

    contours, _ = cv2.findContours(bins, cv2.RETR_TREE, cv2.CHAIN_APPROX_SIMPLE)[-2:]
    hull = [cv2.convexHull(c) for c in contours]
    cv2.drawContours(frame, hull, -1, (0, 255, 0), 2)

    min_area = 400
    max_area = 40000

    vehicle_ids_in_zone = set()

    for cnt in contours:
        area = cv2.contourArea(cnt)
        if min_area < area < max_area:
            M = cv2.moments(cnt)
            if M['m00'] == 0:
                continue
            cx = int(M['m10'] / M['m00'])
            cy = int(M['m01'] / M['m00'])

            matched_id = None
            for vid, info in tracker_dict.items():
                old_cx, old_cy = info['pos']
                if abs(cx - old_cx) < 30 and abs(cy - old_cy) < 30:
                    matched_id = vid
                    break

            if matched_id is None:
                matched_id = vehicle_id_counter
                vehicle_id_counter += 1
                tracker_dict[matched_id] = {
                    'pos': (cx, cy),
                    't1': None,
                    't2': None,
                    'logged': False,
                    'last_cy': cy,
                    'direction': None
                }
            else:
                tracker_dict[matched_id]['pos'] = (cx, cy)

            vehicle = tracker_dict[matched_id]
            last_cy = vehicle['last_cy']
            vehicle['last_cy'] = cy

            if speed_line_y1 <= cy <= speed_line_y2:
                vehicle_ids_in_zone.add(matched_id)

            x, y, w, h = cv2.boundingRect(cnt)
            cv2.rectangle(frame, (x, y), (x + w, y + h), (255, 0, 0), 2)
            cv2.drawMarker(frame, (cx, cy), (0, 0, 255), cv2.MARKER_CROSS, 10, 1)

            # Downward detection
            if not vehicle['t1'] and cy >= speed_line_y1:
                vehicle['t1'] = datetime.now()
            elif not vehicle['t2'] and cy >= speed_line_y2:
                vehicle['t2'] = datetime.now()
                vehicle['direction'] = 'bawah'

            # Upward detection
            if not vehicle['t1'] and cy <= speed_line_y2:
                vehicle['t1'] = datetime.now()
            elif not vehicle['t2'] and cy <= speed_line_y1:
                vehicle['t2'] = datetime.now()
                vehicle['direction'] = 'atas'

            # Speed calculation
            if vehicle['t1'] and vehicle['t2'] and not vehicle['logged']:
                delta_time = (vehicle['t2'] - vehicle['t1']).total_seconds()
                if delta_time > 0:
                    speed_kmh = (meters_travel_pixel / delta_time) * 3.6
                    direction = vehicle['direction'] or 'unknown'
                    print(f"ID {matched_id} SPEED: {speed_kmh:.2f} km/h DIR: {direction}")
                    vehicle['logged'] = True

            # Show ID
            cv2.putText(frame, f"ID:{matched_id}", (x, y - 5),
                        cv2.FONT_HERSHEY_SIMPLEX, 0.4, (0, 255, 255), 1)

            # Show speed
            if vehicle['t1'] and vehicle['t2']:
                delta_time = (vehicle['t2'] - vehicle['t1']).total_seconds()
                if delta_time > 0:
                    speed_kmh = (meters_travel_pixel / delta_time) * 3.6
                    cv2.putText(frame, f"{speed_kmh:.1f} km/h", (x, y + h + 15),
                                cv2.FONT_HERSHEY_SIMPLEX, 0.5, (255, 255, 0), 2)

    # Kepadatan kendaraan per 1km
    kendaraan_dalam_zona = len(vehicle_ids_in_zone)
    panjang_zona_meter = 20  # Panjang zona real di lapangan
    kepadatan_per_meter = kendaraan_dalam_zona / panjang_zona_meter
    kepadatan_per_km = kepadatan_per_meter * 1000

    if kepadatan_per_meter <= 0.05:
        status = "Kepadatan sepi"
        color = (0, 255, 0)
    elif kepadatan_per_meter <= 0.20:
        status = "Kepadatan sedang"
        color = (0, 255, 255)
    else:
        status = "Kepadatan padat"
        color = (0, 0, 255)

    cv2.putText(frame, f"{status} | {kepadatan_per_km:.1f} kendaraan/km", (20, 40),
                cv2.FONT_HERSHEY_SIMPLEX, 0.7, color, 2)

    # Draw detection lines
    cv2.line(frame, (0, speed_line_y1), (width2, speed_line_y1), (0, 255, 255), 2)
    cv2.line(frame, (0, speed_line_y2), (width2, speed_line_y2), (255, 0, 255), 2)

    cv2.imshow("Vehicle Detection", frame)
    if cv2.waitKey(1) & 0xFF == 27:
        break

2025-07-22 08:03:00.245 python[15955:127047] +[IMKClient subclass]: chose IMKClient_Modern
2025-07-22 08:03:00.246 python[15955:127047] +[IMKInputSession subclass]: chose IMKInputSession_Modern


ID 5 SPEED: 9.87 km/h DIR: atas
ID 4 SPEED: 2.63 km/h DIR: atas
ID 6 SPEED: 27.53 km/h DIR: atas
ID 1 SPEED: 0.64 km/h DIR: atas
ID 7 SPEED: 20.07 km/h DIR: bawah
ID 8 SPEED: 28.41 km/h DIR: bawah
ID 10 SPEED: 27.54 km/h DIR: bawah
ID 11 SPEED: 25.37 km/h DIR: bawah
ID 9 SPEED: 1.76 km/h DIR: bawah
ID 12 SPEED: 20.15 km/h DIR: atas
ID 14 SPEED: 15.12 km/h DIR: atas
ID 15 SPEED: 4.08 km/h DIR: atas
ID 16 SPEED: 31.11 km/h DIR: bawah
ID 21 SPEED: 30.09 km/h DIR: bawah
ID 22 SPEED: 29.84 km/h DIR: bawah
ID 23 SPEED: 27.57 km/h DIR: bawah
ID 24 SPEED: 27.69 km/h DIR: bawah
ID 25 SPEED: 25.14 km/h DIR: bawah
ID 26 SPEED: 28.95 km/h DIR: atas
ID 27 SPEED: 25.72 km/h DIR: atas
ID 28 SPEED: 7.05 km/h DIR: bawah
ID 18 SPEED: 0.24 km/h DIR: bawah
ID 2 SPEED: 0.10 km/h DIR: atas
ID 31 SPEED: 18.73 km/h DIR: atas
ID 32 SPEED: 18.70 km/h DIR: atas
ID 33 SPEED: 4705.88 km/h DIR: atas
ID 34 SPEED: 18.94 km/h DIR: bawah
ID 17 SPEED: 0.18 km/h DIR: bawah
ID 37 SPEED: 2.27 km/h DIR: bawah
ID 29 SPEED: 0

## Matikan OpenCV

In [12]:
cap.release()
cv2.destroyAllWindows()